In [1]:
import platform

import numpy as np

import plotly.graph_objects as go
import os
import plotly.io as pio
from plotly.subplots import make_subplots

import scipy
from scipy import optimize, stats
from scipy.stats import chi2, logistic, norm

# Plotly rendering (CKC convention)
pio.templates.default = "plotly_white"
pio.renderers.default = os.environ.get("PLOTLY_RENDERER", "notebook")

# Reproducibility
rng = np.random.default_rng(7)
np.set_printoptions(precision=4, suppress=True)

print("Python", platform.python_version())
print("NumPy", np.__version__)
print("SciPy", scipy.__version__)


Python 3.12.9
NumPy 1.26.2
SciPy 1.15.0


In [2]:
def sigmoid(z: np.ndarray) -> np.ndarray:
    # Stable logistic function σ(z) = 1 / (1 + exp(-z)).

    z = np.asarray(z, dtype=float)
    out = np.empty_like(z)

    pos = z >= 0
    out[pos] = 1.0 / (1.0 + np.exp(-z[pos]))

    ez = np.exp(z[~pos])
    out[~pos] = ez / (1.0 + ez)

    return out


def logistic_cdf(x: np.ndarray, mu: float = 0.0, s: float = 1.0) -> np.ndarray:
    if s <= 0:
        raise ValueError("scale s must be > 0")
    z = (np.asarray(x, dtype=float) - mu) / s
    return sigmoid(z)


def logistic_pdf(x: np.ndarray, mu: float = 0.0, s: float = 1.0) -> np.ndarray:
    if s <= 0:
        raise ValueError("scale s must be > 0")
    z = (np.asarray(x, dtype=float) - mu) / s
    p = sigmoid(z)
    return (p * (1.0 - p)) / s


def logistic_logpdf(x: np.ndarray, mu: float = 0.0, s: float = 1.0) -> np.ndarray:
    # Stable log-PDF using logaddexp:
    # log f(x) = -log s - z - 2 log(1 + exp(-z)), where z=(x-mu)/s.

    if s <= 0:
        raise ValueError("scale s must be > 0")
    z = (np.asarray(x, dtype=float) - mu) / s
    return -np.log(s) - z - 2.0 * np.logaddexp(0.0, -z)


def logistic_ppf(p: np.ndarray, mu: float = 0.0, s: float = 1.0, eps: float = 1e-12) -> np.ndarray:
    if s <= 0:
        raise ValueError("scale s must be > 0")
    p = np.asarray(p, dtype=float)
    p = np.clip(p, eps, 1.0 - eps)
    return mu + s * (np.log(p) - np.log1p(-p))


def logistic_rvs(
    rng: np.random.Generator,
    size: int | tuple[int, ...],
    mu: float = 0.0,
    s: float = 1.0,
) -> np.ndarray:
    # NumPy-only sampling via inverse CDF.

    u = rng.random(size=size)
    return logistic_ppf(u, mu=mu, s=s)


def logistic_moments(mu: float = 0.0, s: float = 1.0) -> dict:
    if s <= 0:
        raise ValueError("scale s must be > 0")

    mean = mu
    var = (np.pi * s) ** 2 / 3.0

    return {
        "mean": mean,
        "variance": var,
        "skewness": 0.0,
        "kurtosis": 4.2,  # non-excess
        "excess_kurtosis": 6.0 / 5.0,
        "median": mu,
        "mode": mu,
    }


def logistic_entropy(s: float = 1.0) -> float:
    if s <= 0:
        raise ValueError("scale s must be > 0")
    return float(np.log(s) + 2.0)


def logistic_mgf(t: np.ndarray, mu: float = 0.0, s: float = 1.0) -> np.ndarray:
    # MGF M_X(t) = E[e^{tX}] for |t| < 1/s.

    if s <= 0:
        raise ValueError("scale s must be > 0")

    t = np.asarray(t, dtype=float)
    x = np.pi * s * t

    out = np.full_like(t, np.nan, dtype=float)
    ok = np.abs(t) < (1.0 / s)

    ratio = np.empty_like(x)
    small = np.abs(x) < 1e-4
    ratio[small] = 1.0 + (x[small] ** 2) / 6.0 + 7.0 * (x[small] ** 4) / 360.0
    ratio[~small] = x[~small] / np.sin(x[~small])

    out[ok] = np.exp(mu * t[ok]) * ratio[ok]
    return out


def logistic_cf(t: np.ndarray, mu: float = 0.0, s: float = 1.0) -> np.ndarray:
    # Characteristic function φ_X(t) = E[e^{itX}] for real t.

    if s <= 0:
        raise ValueError("scale s must be > 0")

    t = np.asarray(t, dtype=float)
    x = np.pi * s * t

    ratio = np.empty_like(x)
    small = np.abs(x) < 1e-4
    ratio[small] = 1.0 - (x[small] ** 2) / 6.0 + 7.0 * (x[small] ** 4) / 360.0
    ratio[~small] = x[~small] / np.sinh(x[~small])

    return np.exp(1j * mu * t) * ratio


In [3]:
# Quick numerical checks: moments + MGF (Monte Carlo)
mu0, s0 = 0.7, 1.3
n = 200_000

samples = logistic_rvs(rng, size=n, mu=mu0, s=s0)

mom = logistic_moments(mu=mu0, s=s0)
mean_mc = samples.mean()
var_mc = samples.var(ddof=0)

skew_mc = stats.skew(samples)
kurt_mc = stats.kurtosis(samples, fisher=False)  # non-excess

mom, mean_mc, var_mc, skew_mc, kurt_mc


({'mean': 0.7,
  'variance': 5.559877145947005,
  'skewness': 0.0,
  'kurtosis': 4.2,
  'excess_kurtosis': 1.2,
  'median': 0.7,
  'mode': 0.7},
 0.703193870225651,
 5.502046897613281,
 -0.004496053448897028,
 4.170427457166342)

In [4]:
# MGF check for a few t in the valid range |t| < 1/s
# (Monte Carlo estimate: mean(exp(tX)))

ts = np.array([-0.4, -0.2, 0.2, 0.4]) / s0  # safely within (-1/s, 1/s)

mgf_theory = logistic_mgf(ts, mu=mu0, s=s0)
mgf_mc = np.array([np.mean(np.exp(t * samples)) for t in ts])

np.column_stack([ts, mgf_theory, mgf_mc])


array([[-0.3077,  1.0653,  1.0606],
       [-0.1538,  0.9598,  0.9587],
       [ 0.1538,  1.1905,  1.1902],
       [ 0.3077,  1.6389,  1.6343]])

In [5]:
# Useful scale relationships

def logistic_sd(s: float) -> float:
    return float(np.pi * s / np.sqrt(3.0))


def logistic_iqr(s: float) -> float:
    return float(2.0 * s * np.log(3.0))

for s in [0.5, 1.0, 2.0]:
    print(f"s={s:>4}: sd={logistic_sd(s):.4f}, IQR={logistic_iqr(s):.4f}")


s= 0.5: sd=0.9069, IQR=1.0986
s= 1.0: sd=1.8138, IQR=2.1972
s= 2.0: sd=3.6276, IQR=4.3944


In [6]:
def logistic_loglik(x: np.ndarray, mu: float, s: float) -> float:
    return float(np.sum(logistic_logpdf(x, mu=mu, s=s)))


def fit_logistic_mle(x: np.ndarray, mu_init: float | None = None, s_init: float | None = None):
    x = np.asarray(x, dtype=float)

    if mu_init is None:
        mu_init = float(np.median(x))
    if s_init is None:
        s_init = float(np.std(x, ddof=0) * np.sqrt(3.0) / np.pi)
        s_init = max(s_init, 1e-3)

    def nll(theta: np.ndarray) -> float:
        mu, log_s = float(theta[0]), float(theta[1])
        s = float(np.exp(log_s))
        return -logistic_loglik(x, mu=mu, s=s)

    res = optimize.minimize(nll, x0=np.array([mu_init, np.log(s_init)]), method="BFGS")
    mu_hat, log_s_hat = res.x
    return {
        "mu_hat": float(mu_hat),
        "s_hat": float(np.exp(log_s_hat)),
        "success": bool(res.success),
        "message": res.message,
        "fun": float(res.fun),
    }


# Compare our simple MLE to SciPy's fit on simulated data
x_data = logistic_rvs(rng, size=5_000, mu=1.2, s=0.8)

ours = fit_logistic_mle(x_data)
scipy_loc, scipy_scale = stats.logistic.fit(x_data)

ours, (scipy_loc, scipy_scale)


({'mu_hat': 1.2258002867931699,
  's_hat': 0.7831215632335,
  'success': True,
  'message': 'Optimization terminated successfully.',
  'fun': 8783.809900252894},
 (1.2258003058433171, 0.7831215768119856))

In [7]:
# Sampling sanity checks
mu0, s0 = -0.5, 1.7

x = logistic_rvs(rng, size=200_000, mu=mu0, s=s0)

# 1) Mean/variance
print('mean (mc)', x.mean(), 'theory', logistic_moments(mu0, s0)['mean'])
print('var  (mc)', x.var(ddof=0), 'theory', logistic_moments(mu0, s0)['variance'])

# 2) Probability integral transform: F(X) should look Uniform(0,1)
u = logistic_cdf(x, mu=mu0, s=s0)
print('u mean', u.mean(), 'u var', u.var(ddof=0))

# Compare a few quantiles to Uniform(0,1)
qs = np.array([0.01, 0.1, 0.5, 0.9, 0.99])
print('empirical u-quantiles:', np.quantile(u, qs))
print('target quantiles     :', qs)


mean (mc) -0.5094692359972378 theory -0.5
var  (mc) 9.4866561100536 theory 9.507718906382747
u mean 0.4992795266980339 u var 0.08335766686663254
empirical u-quantiles: [0.0099 0.0994 0.4993 0.8989 0.99  ]
target quantiles     : [0.01 0.1  0.5  0.9  0.99]


In [8]:
# PDF/CDF for several parameter choices

params = [
    (0.0, 0.6),
    (0.0, 1.0),
    (0.0, 2.0),
    (2.0, 1.0),
]

# choose an x-range that covers all cases (0.001 to 0.999 quantiles)
lo = min(logistic_ppf(1e-3, mu=mu, s=s) for mu, s in params)
hi = max(logistic_ppf(1 - 1e-3, mu=mu, s=s) for mu, s in params)
xx = np.linspace(lo, hi, 800)

fig = make_subplots(rows=1, cols=2, subplot_titles=("PDF", "CDF"))

for mu, s in params:
    label = f"μ={mu}, s={s}"
    fig.add_trace(go.Scatter(x=xx, y=logistic_pdf(xx, mu=mu, s=s), mode="lines", name=label), row=1, col=1)
    fig.add_trace(go.Scatter(x=xx, y=logistic_cdf(xx, mu=mu, s=s), mode="lines", showlegend=False), row=1, col=2)

fig.update_xaxes(title_text="x", row=1, col=1)
fig.update_xaxes(title_text="x", row=1, col=2)
fig.update_yaxes(title_text="density", row=1, col=1)
fig.update_yaxes(title_text="probability", row=1, col=2)

fig.update_layout(title="Logistic distribution: PDF and CDF", width=950, height=420)
fig.show()


In [9]:
# Monte Carlo histogram + PDF overlay

mu0, s0 = 0.0, 1.0
samples_mc = logistic_rvs(rng, size=80_000, mu=mu0, s=s0)

x_grid = np.linspace(logistic_ppf(1e-4, mu0, s0), logistic_ppf(1 - 1e-4, mu0, s0), 900)

fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=samples_mc,
        nbinsx=70,
        histnorm="probability density",
        name="Monte Carlo (NumPy-only)",
        opacity=0.55,
    )
)
fig.add_trace(
    go.Scatter(
        x=x_grid,
        y=logistic_pdf(x_grid, mu=mu0, s=s0),
        mode="lines",
        name="True PDF",
        line=dict(width=3),
    )
)

fig.update_layout(title=f"Logistic(μ={mu0}, s={s0}): histogram vs PDF", width=900, height=420)
fig.show()


In [10]:
# CDF: theoretical vs empirical

x_grid = np.linspace(logistic_ppf(1e-4, mu0, s0), logistic_ppf(1 - 1e-4, mu0, s0), 700)

emp_x = np.sort(samples_mc)
emp_cdf = np.arange(1, emp_x.size + 1) / emp_x.size

fig = go.Figure()
fig.add_trace(go.Scatter(x=x_grid, y=logistic_cdf(x_grid, mu=mu0, s=s0), mode="lines", name="True CDF"))
fig.add_trace(
    go.Scatter(
        x=emp_x[::200],
        y=emp_cdf[::200],
        mode="markers",
        name="Empirical CDF (subsampled)",
        marker=dict(size=4, opacity=0.55),
    )
)

fig.update_layout(title=f"Logistic(μ={mu0}, s={s0}): CDF vs empirical", width=900, height=420)
fig.show()


In [11]:
dist = stats.logistic(loc=mu0, scale=s0)

x_test = np.linspace(-2, 2, 5)

pdf = dist.pdf(x_test)
cdf = dist.cdf(x_test)
samples_scipy = dist.rvs(size=5, random_state=rng)

pdf, cdf, samples_scipy


(array([0.105 , 0.1966, 0.25  , 0.1966, 0.105 ]),
 array([0.1192, 0.2689, 0.5   , 0.7311, 0.8808]),
 array([-0.9978,  1.6964, -1.7808, -1.3917, -2.842 ]))

In [12]:
# MLE fit example
true_mu, true_s = 1.5, 0.9
x_fit = stats.logistic(loc=true_mu, scale=true_s).rvs(size=10_000, random_state=rng)

mu_hat, s_hat = stats.logistic.fit(x_fit)  # returns (loc, scale)

true_mu, true_s, mu_hat, s_hat


(1.5, 0.9, 1.5159770568469728, 0.9025679317202033)

In [13]:
# 10.1 Likelihood-ratio test example: H0: mu = 0

rng_test = np.random.default_rng(123)

n = 400
mu_true, s_true = 0.35, 1.0
x = logistic_rvs(rng_test, size=n, mu=mu_true, s=s_true)


def mle_unrestricted(x: np.ndarray):
    x = np.asarray(x, dtype=float)

    def nll(theta: np.ndarray) -> float:
        mu, log_s = float(theta[0]), float(theta[1])
        s = float(np.exp(log_s))
        return -logistic_loglik(x, mu=mu, s=s)

    mu_init = float(np.median(x))
    s_init = float(np.std(x, ddof=0) * np.sqrt(3.0) / np.pi)

    res = optimize.minimize(nll, x0=np.array([mu_init, np.log(max(s_init, 1e-3))]), method="BFGS")
    mu_hat, log_s_hat = res.x
    return float(mu_hat), float(np.exp(log_s_hat)), float(-res.fun)


def mle_mu_fixed(x: np.ndarray, mu0: float):
    x = np.asarray(x, dtype=float)

    def nll(log_s: np.ndarray) -> float:
        s = float(np.exp(float(log_s)))
        return -logistic_loglik(x, mu=mu0, s=s)

    s_init = float(np.std(x, ddof=0) * np.sqrt(3.0) / np.pi)
    res = optimize.minimize(nll, x0=np.array([np.log(max(s_init, 1e-3))]), method="BFGS")
    s_hat = float(np.exp(float(res.x)))
    return s_hat, float(-res.fun)


mu0 = 0.0
mu_hat, s_hat, ll1 = mle_unrestricted(x)
s_tilde, ll0 = mle_mu_fixed(x, mu0=mu0)

lrt = 2.0 * (ll1 - ll0)
p_value = 1.0 - chi2.cdf(lrt, df=1)

{
    "n": n,
    "true": (mu_true, s_true),
    "mle_unrestricted": (mu_hat, s_hat),
    "mle_H0": (mu0, s_tilde),
    "LRT": lrt,
    "p_value": p_value,
}


/tmp/ipykernel_1031270/2293021024.py:30: DeprecationWarning:

Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)

/tmp/ipykernel_1031270/2293021024.py:35: DeprecationWarning:

Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)



{'n': 400,
 'true': (0.35, 1.0),
 'mle_unrestricted': (0.26463042446936813, 0.9882888911189841),
 'mle_H0': (0.0, 0.9992910134947958),
 'LRT': 9.410232061566376,
 'p_value': 0.0021577791606112173}

In [14]:
# 10.2 Bayesian example: posterior over mu with known scale (grid approximation)

x = logistic_rvs(rng, size=200, mu=0.6, s=1.0)
s_known = 1.0

# Prior: mu ~ Normal(0, 2^2)
mu_grid = np.linspace(-2.5, 2.5, 1201)
log_prior = norm(loc=0.0, scale=2.0).logpdf(mu_grid)

# Log-likelihood for each mu on the grid
log_like = np.array([logistic_loglik(x, mu=mu, s=s_known) for mu in mu_grid])
log_post_unnorm = log_prior + log_like
log_post = log_post_unnorm - np.max(log_post_unnorm)
post = np.exp(log_post)
post /= post.sum()

post_mean = float(np.sum(mu_grid * post))
post_cdf = np.cumsum(post)
ci_low = float(mu_grid[np.searchsorted(post_cdf, 0.025)])
ci_high = float(mu_grid[np.searchsorted(post_cdf, 0.975)])

(post_mean, (ci_low, ci_high))


(0.5288318801511985, (0.2875000000000001, 0.7708333333333335))

In [15]:
# Visualize the posterior

fig = go.Figure()
fig.add_trace(go.Scatter(x=mu_grid, y=post, mode="lines", name="posterior"))
fig.add_vline(x=post_mean, line_dash="dash", line_color="black", annotation_text="posterior mean")
fig.add_vrect(x0=ci_low, x1=ci_high, fillcolor="gray", opacity=0.2, line_width=0)

fig.update_layout(
    title="Posterior over μ (known s): grid approximation",
    xaxis_title="μ",
    yaxis_title="posterior density (discrete grid)",
    width=900,
    height=420,
)
fig.show()


In [16]:
# 10.3 Generative modeling: a simple mixture of logistics

weights = np.array([0.55, 0.45])
components = [(-1.2, 0.6), (1.4, 0.9)]  # (mu, s)


def mixture_logistic_pdf(x: np.ndarray) -> np.ndarray:
    x = np.asarray(x, dtype=float)
    out = np.zeros_like(x)
    for w, (mu, s) in zip(weights, components):
        out += w * logistic_pdf(x, mu=mu, s=s)
    return out


def mixture_logistic_rvs(rng: np.random.Generator, size: int) -> np.ndarray:
    k = rng.choice(len(weights), size=size, p=weights)
    out = np.empty(size, dtype=float)
    for idx in range(len(weights)):
        mask = k == idx
        mu, s = components[idx]
        out[mask] = logistic_rvs(rng, size=int(mask.sum()), mu=mu, s=s)
    return out


mix_samples = mixture_logistic_rvs(rng, size=60_000)

x_grid = np.linspace(np.quantile(mix_samples, 0.001), np.quantile(mix_samples, 0.999), 900)

fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=mix_samples,
        nbinsx=90,
        histnorm="probability density",
        name="samples",
        opacity=0.55,
    )
)
fig.add_trace(go.Scatter(x=x_grid, y=mixture_logistic_pdf(x_grid), mode="lines", name="mixture PDF", line=dict(width=3)))

fig.update_layout(title="Mixture of logistics: histogram vs PDF", width=900, height=420)
fig.show()
